In [79]:
import pandas as pd
from sklearn.model_selection import train_test_split
import re
import nltk
from nltk.tokenize import word_tokenize
from collections import Counter


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Aymane\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [5]:
df = pd.read_csv('bbc_data.csv')

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2225 entries, 0 to 2224
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   data    2225 non-null   object
 1   labels  2225 non-null   object
dtypes: object(2)
memory usage: 34.9+ KB


In [58]:
df

data         labels
0     Musicians to tackle US red tape  Musicians gro...  entertainment
1     U2s desire to be number one  U2, who have won ...  entertainment
2     Rocker Doherty in on-stage fight  Rock singer ...  entertainment
3     Snicket tops US box office chart  The film ada...  entertainment
4     Oceans Twelve raids box office  Oceans Twelve,...  entertainment
...                                                 ...            ...
2220  Warning over Windows Word files  Writing a Mic...           tech
2221  Fast lifts rise into record books  Two high-sp...           tech
2222  Nintendo adds media playing to DS  Nintendo is...           tech
2223  Fast moving phone viruses appear  Security fir...           tech
2224  Hacker threat to Apples iTunes  Users of Apple...           tech

[2225 rows x 2 columns]

In [48]:
y = df['labels']
X = df['data']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [53]:
print(y_train)

1490    politics
2001        tech
1572    politics
1840        tech
610     business
          ...   
1638    politics
1095       sport
1130       sport
1294       sport
860     business
Name: labels, Length: 1780, dtype: object


Calculating the prior probability

In [54]:
classes = y_train.unique()
y_train_df = pd.DataFrame(y_train)
counts = {}
for label in classes :
    counts[label] = len(y_train_df[y_train_df['labels'] == label])

print(counts)

{'politics': 337, 'tech': 321, 'business': 407, 'entertainment': 302, 'sport': 413}


In [55]:
class_probability = {}
total_nbr = sum(list(counts.values()))
for label in classes:
    class_probability[label] = counts[label] / total_nbr
print(class_probability)

{'politics': 0.18932584269662922, 'tech': 0.18033707865168538, 'business': 0.22865168539325842, 'entertainment': 0.1696629213483146, 'sport': 0.23202247191011235}


Calculating likelihoods given a class (Laplace add-1 included) 

Regrouping text per class

In [75]:
text_per_class = {}
df_train = pd.concat([X_train,y_train],axis = 1)
for label in classes :
    text_per_class[label] = ''
for label in classes :
    text_class = df_train[df_train['labels']== label]
    texts = text_class['data']
    for text in texts:
        text_per_class[label] += str(text)




Blair hails Turkey-EU talks deal  Tony Blair has hailed a deal bringing Turkey a step closer to EU membership as important for the worlds future "peace and prosperity".  Mr Blair has been a leading advocate of Turkish membership despite controversy surrounding the idea. Leaving a Brussels summit Mr Blair said "the fact Turkey is a Muslim country does not mean it should be barred". The deal to open formal talks with Ankara came despite an EU demand for Turkey to recognise Cyprus. It was agreed the issue can be tackled at a later date but Turkish premier Recep Erdogan had to accept negotiations did not guarantee his country full EU membership.  If it joins, Turkey may have to accept restrictions to limit migration by its citizens. Mr Blair said having Turkey in the EU was of "importance to the future peace and prosperity of my country, Britain, and the wider world".  "We are stating a fundamental principle that the fact Turkey is a Muslim country does not mean it should be barred from Eu

Remove punct and apply case folding

In [77]:
for label in classes:
    
    text = text_per_class[label]
    text = re.sub(r'[^\w\s]',' ',text)
    text_per_class[label] = text.lower()
print(text_per_class['politics'])
  

blair hails turkey eu talks deal  tony blair has hailed a deal bringing turkey a step closer to eu membership as important for the worlds future  peace and prosperity    mr blair has been a leading advocate of turkish membership despite controversy surrounding the idea  leaving a brussels summit mr blair said  the fact turkey is a muslim country does not mean it should be barred   the deal to open formal talks with ankara came despite an eu demand for turkey to recognise cyprus  it was agreed the issue can be tackled at a later date but turkish premier recep erdogan had to accept negotiations did not guarantee his country full eu membership   if it joins  turkey may have to accept restrictions to limit migration by its citizens  mr blair said having turkey in the eu was of  importance to the future peace and prosperity of my country  britain  and the wider world     we are stating a fundamental principle that the fact turkey is a muslim country does not mean it should be barred from eu

Tokens per class

In [80]:
# nltk.download('punkt')
tokens_per_class = {}
for label in classes :
    text = text_per_class[label]
    tokenized = word_tokenize(text)
    tokens_per_class[label] = tokenized
print(tokens_per_class['politics'])


['blair', 'hails', 'turkey', 'eu', 'talks', 'deal', 'tony', 'blair', 'has', 'hailed', 'a', 'deal', 'bringing', 'turkey', 'a', 'step', 'closer', 'to', 'eu', 'membership', 'as', 'important', 'for', 'the', 'worlds', 'future', 'peace', 'and', 'prosperity', 'mr', 'blair', 'has', 'been', 'a', 'leading', 'advocate', 'of', 'turkish', 'membership', 'despite', 'controversy', 'surrounding', 'the', 'idea', 'leaving', 'a', 'brussels', 'summit', 'mr', 'blair', 'said', 'the', 'fact', 'turkey', 'is', 'a', 'muslim', 'country', 'does', 'not', 'mean', 'it', 'should', 'be', 'barred', 'the', 'deal', 'to', 'open', 'formal', 'talks', 'with', 'ankara', 'came', 'despite', 'an', 'eu', 'demand', 'for', 'turkey', 'to', 'recognise', 'cyprus', 'it', 'was', 'agreed', 'the', 'issue', 'can', 'be', 'tackled', 'at', 'a', 'later', 'date', 'but', 'turkish', 'premier', 'recep', 'erdogan', 'had', 'to', 'accept', 'negotiations', 'did', 'not', 'guarantee', 'his', 'country', 'full', 'eu', 'membership', 'if', 'it', 'joins', 'tu

In [82]:
frequences_per_class = {label: {} for label in classes}

for label in classes:
    tokens = tokens_per_class[label]  
    frequences_per_class[label] = dict(Counter(tokens))  #
vocabulary = set()
for tokens in tokens_per_class.values():
    vocabulary.update(tokens)  

for label in classes:
    for token in vocabulary:
        if token in frequences_per_class[label]:
            frequences_per_class[label][token] += 1  
        else:
            frequences_per_class[label][token] = 1 

print(frequences_per_class)

{'politics': {'blair': 449, 'hails': 2, 'turkey': 20, 'eu': 98, 'talks': 34, 'deal': 75, 'tony': 159, 'has': 790, 'hailed': 4, 'a': 3208, 'bringing': 10, 'step': 29, 'closer': 10, 'to': 4846, 'membership': 17, 'as': 882, 'important': 59, 'for': 1549, 'the': 9744, 'worlds': 21, 'future': 61, 'peace': 33, 'and': 3243, 'prosperity': 15, 'mr': 1411, 'been': 472, 'leading': 19, 'advocate': 5, 'of': 3567, 'turkish': 6, 'despite': 42, 'controversy': 18, 'surrounding': 9, 'idea': 38, 'leaving': 14, 'brussels': 6, 'summit': 11, 'said': 1803, 'fact': 35, 'is': 1489, 'muslim': 28, 'country': 145, 'does': 56, 'not': 944, 'mean': 38, 'it': 1180, 'should': 296, 'be': 1358, 'barred': 3, 'open': 42, 'formal': 7, 'with': 819, 'ankara': 3, 'came': 52, 'an': 527, 'demand': 10, 'recognise': 18, 'cyprus': 7, 'was': 1271, 'agreed': 34, 'issue': 138, 'can': 293, 'tackled': 7, 'at': 682, 'later': 60, 'date': 31, 'but': 853, 'premier': 11, 'recep': 3, 'erdogan': 3, 'had': 605, 'accept': 27, 'negotiations': 15,

In [84]:
probability_per_class = {label: {} for label in classes}

total_frequencies_per_class = {label: sum(frequences_per_class[label].values()) for label in classes}

for label in classes:
    for token in frequences_per_class[label]:
        probability_per_class[label][token] = (
            frequences_per_class[label][token] / (total_frequencies_per_class[label] + len(vocabulary))
        )

print(probability_per_class['politics'])


{'blair': 0.0021295870308624116, 'hails': 9.485911050612079e-06, 'turkey': 9.485911050612078e-05, 'eu': 0.00046480964147999185, 'talks': 0.00016126048786040532, 'deal': 0.0003557216643979529, 'tony': 0.0007541299285236603, 'has': 0.003746934864991771, 'hailed': 1.8971822101224158e-05, 'a': 0.015215401325181774, 'bringing': 4.742955525306039e-05, 'step': 0.00013754571023387514, 'closer': 4.742955525306039e-05, 'to': 0.022984362475633065, 'membership': 8.063024393020266e-05, 'as': 0.004183286773319927, 'important': 0.0002798343759930563, 'for': 0.007346838108699055, 'the': 0.046215358638582046, 'worlds': 9.960206603142683e-05, 'future': 0.0002893202870436684, 'peace': 0.0001565175323350993, 'and': 0.015381404768567485, 'prosperity': 7.114433287959059e-05, 'mr': 0.006692310246206821, 'been': 0.0022386750079444505, 'leading': 9.011615498081475e-05, 'advocate': 2.3714777626530195e-05, 'of': 0.016918122358766642, 'turkish': 2.8457733151836237e-05, 'despite': 0.00019920413206285365, 'controve